# Content-based recommenders

Content-based recommenders in their recommendations rely purely on the features of users and items. Conceptually it can be expressed as a model of the form (personalized):

<center>
$$
    score \sim (user\_feature\_1, user\_feature\_2, ..., user\_feature\_k, item\_feature_1, item\_feature_2, ..., item\_feature_n)
$$
</center>

or (not personalized)

<center>
$$
    score \sim (item\_feature_1, item\_feature_2, ..., item\_feature_n)
$$
</center>


    + Content-based recommenders do not suffer from the cold-start problem for new items.
    - They do not use information about complex patterns of user-item interactions - what other similar users have already
    discovered and liked.

In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from IPython.display import Markdown, display, HTML
from collections import defaultdict
from sklearn.model_selection import KFold
import time

pd.set_option('display.max_columns', 50)

from evaluation_and_testing.testing import evaluate_train_test_split_explicit
from evaluation_and_testing.testing import evaluate_leave_one_out_explicit
from evaluation_and_testing.testing import evaluate_train_test_split_implicit
from evaluation_and_testing.testing import evaluate_leave_one_out_implicit

# Fix the dying kernel problem (only a problem in some installations - you can remove it, if it works without it)
import os
os.environ['KMP_DUPLICATE_LIB_OK'] = 'True'

# Load the data

In [2]:
ml_ratings_df = pd.read_csv(os.path.join("data", "movielens_small", "ratings.csv")).rename(columns={'userId': 'user_id', 'movieId': 'item_id'})
ml_movies_df = pd.read_csv(os.path.join("data", "movielens_small", "movies.csv")).rename(columns={'movieId': 'item_id'})
ml_df = pd.merge(ml_ratings_df, ml_movies_df, on='item_id')

display(ml_movies_df.head(10))

# Filter the data to reduce the number of movies
seed = 6789
rng = np.random.RandomState(seed=seed)
left_ids = rng.choice(ml_movies_df['item_id'], size=1000, replace=False)

ml_ratings_df = ml_ratings_df.loc[ml_ratings_df['item_id'].isin(left_ids)]
ml_movies_df = ml_movies_df.loc[ml_movies_df['item_id'].isin(left_ids)]
ml_df = ml_df.loc[ml_df['item_id'].isin(left_ids)]

print("Number of chosen interactions: {}".format(len(ml_ratings_df)))

item_id                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   
5        6                         Heat (1995)   
6        7                      Sabrina (1995)   
7        8                 Tom and Huck (1995)   
8        9                 Sudden Death (1995)   
9       10                    GoldenEye (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy  
5                        Action|Crime|Thriller  
6                               Comedy|Romance  
7                           Adventure|Children  
8                                       Action  
9                    Action|Adventure|Thriller

Number of chosen interactions: 9692


# Linear Regression Recommender

For every movie we transform its genres into one-hot encoded features and we normalize them, for every user we count percentages for all genres how often do they appear among films watched by the user, we multiply both vectors (for the item and the user) to obtain explanaytory variables, and then we fit a linear regression model to those features and actual ratings.

In [21]:
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import MultiLabelBinarizer

from recommenders.recommender import Recommender

class LinearRegressionRecommender(Recommender):
    """
    Linear regression recommender class.
    """
    
    def __init__(self):
        """
        Initialize recommender params and variables.
        """
        self.model = None
        self.mlb = None
        self.users_dict = None
        self.user_features = None
        
        self.uses_dot_product = True
    
    def fit(self, interactions_df, users_df, items_df):
        """
        Training of the recommender.
        
        :param pd.DataFrame interactions_df: DataFrame with recorded interactions between users and items 
            defined by user_id, item_id and features of the interaction.
        :param pd.DataFrame users_df: DataFrame with users and their features defined by user_id and the user feature columns.
        :param pd.DataFrame items_df: DataFrame with items and their features defined by item_id and the item feature columns.
        """
        
        # Transform genres to a more code-friendly form
        
        interactions_df = pd.merge(interactions_df, items_df, on='item_id')
        interactions_df = self._transform_genres(interactions_df)
        
        # Prepare user features
        
        users_df = interactions_df[['user_id', 'genres']].copy()
        users_df = users_df.explode('genres')
        users_df['val'] = 1
        users_df = users_df.pivot_table(index='user_id', columns='genres', values='val', aggfunc='count')
        users_df = users_df / users_df.sum(axis=1).values.reshape(-1, 1)
        
        users_df = users_df.rename_axis(None, axis=1).fillna(0)
        users_df = users_df.add_prefix('user_')
#         display(users_df.head(10))
        display(users_df)
        self.users_dict = users_df.to_dict('index')
        
        self.user_features = users_df.columns.tolist()
       
        interactions_df = interactions_df.merge(users_df, on='user_id')
#         display(interactions_df.head(10))
                
        # Prepare item features
        
        # Transform genres into binary values
        
        self.mlb = MultiLabelBinarizer()
        interactions_df = interactions_df.join(
            pd.DataFrame(self.mlb.fit_transform(interactions_df.pop('genres')),
                         columns=self.mlb.classes_,
                         index=interactions_df.index))
        
        # Normalize the values so that each movie's genres sum up to 1
        
        interactions_df[self.mlb.classes_] = interactions_df[self.mlb.classes_] \
            / interactions_df[self.mlb.classes_].sum(axis=1).values.reshape(-1, 1)
        
#         display(interactions_df.loc[:, self.mlb.classes_].head(10))

        # Prepare input data and fit the model
    
        # Dot product for personalization
        if self.uses_dot_product:
            interactions_df[self.mlb.classes_] = interactions_df[self.mlb.classes_] \
                * interactions_df[self.user_features].values
    
#         display(interactions_df.head(10))
        
        if self.uses_dot_product:  # Personalized
            x = interactions_df.loc[:, self.mlb.classes_].values
        else:  # Non-personalized
            x = interactions_df.loc[:, list(self.mlb.classes_) + self.user_features].values
        
        y = interactions_df['rating'].values
    
        self.model = LinearRegression().fit(x, y)
    
    def recommend(self, users_df, items_df, n_recommendations=1):
        """
        Serving of recommendations. Scores items in items_df for each user in users_df and returns 
        top n_recommendations for each user.
        
        :param pd.DataFrame users_df: DataFrame with users and their features for which recommendations should be generated.
        :param pd.DataFrame items_df: DataFrame with items and their features which should be scored.
        :param int n_recommendations: Number of recommendations to be returned for each user.
        :return: DataFrame with user_id, item_id and score as columns returning n_recommendations top recommendations 
            for each user.
        :rtype: pd.DataFrame
        """
        
        # Transform the item to be scored into proper features
        
        items_df = items_df.copy()
        items_df = self._transform_genres(items_df)
        
        items_df = items_df.join(
            pd.DataFrame(self.mlb.transform(items_df.pop('genres')),
                         columns=self.mlb.classes_,
                         index=items_df.index))
        
        items_df[self.mlb.classes_] = items_df[self.mlb.classes_] \
            / items_df[self.mlb.classes_].sum(axis=1).values.reshape(-1, 1)
        display(items_df)
        # Score the item
    
        recommendations = pd.DataFrame(columns=['user_id', 'item_id', 'score'])
        
        for ix, user in users_df.iterrows():
            if user['user_id'] in self.users_dict:
                user_df = pd.DataFrame.from_dict({user['user_id']: self.users_dict[user['user_id']]}, orient='index')
            else:
                user_df = pd.DataFrame.from_dict(
                    {user['user_id']: [1 / len(self.user_features)]*len(self.user_features)}, orient='index')
                user_df.columns = self.user_features
#             display(user_df)
#             display(items_df)
            input_df = items_df.copy()
            
            if self.uses_dot_product:
                input_df[self.mlb.classes_] = items_df[self.mlb.classes_] * user_df.values
#                 display(input_df)
                scores = self.model.predict(input_df.loc[:, self.mlb.classes_].values)
            else:
                input_df = input_df.merge(user_df, how='cross')
#                 display(input_df)
                scores = self.model.predict(input_df.loc[:, list(self.mlb.classes_) + self.user_features].values)
    
            chosen_pos = np.argsort(-scores)[:n_recommendations]
        
            user_recommendations = []
            for item_pos in chosen_pos:
                user_recommendations.append(
                    {
                        'user_id': user['user_id'],
                        'item_id': input_df.iloc[item_pos]['item_id'],
                        'score': scores[item_pos]
                    }
                )
                
            user_recommendations = pd.DataFrame(user_recommendations)

            recommendations = pd.concat([recommendations, user_recommendations])

        return recommendations
    
    def _transform_genres(self, df):
        """
        Transforms a string with genres into a list of cleaned genre names.
        
        :param pd.DataFrame df: A DataFrame with 'genres' column.
        """
        df.loc[:, 'genres'] = df['genres'].str.replace("-", "_", regex=False)
        df.loc[:, 'genres'] = df['genres'].str.replace(" ", "_", regex=False)
        df.loc[:, 'genres'] = df['genres'].str.replace("(", "", regex=False)
        df.loc[:, 'genres'] = df['genres'].str.replace(")", "", regex=False)
        df.loc[:, 'genres'] = df['genres'].str.lower()
        df.loc[:, 'genres'] = df['genres'].str.split("|")
        return df

In [4]:
# Print movies watched by user 3, 5, 39

active_user_movies = ml_df.loc[
    (ml_df['user_id'] == 3) | (ml_df['user_id'] == 5) | (ml_df['user_id'] == 39)].sort_values(['user_id', 'item_id'])
print("Active users history")
display(active_user_movies)

Active users history


user_id  item_id  rating   timestamp  \
18810        3     5181     5.0  1306463718   
18827        3     7991     5.0  1306463684   
18832        3    70946     5.0  1306463815   
573          5       50     4.0   847434881   
19321        5      232     4.0   847435292   
25824        5      266     1.0   847435311   
19722        5      475     5.0   847435311   
20123        5      595     5.0   847434832   
588         39       50     5.0   974788030   
45366       39      858     4.0   974789111   
7762        39     1213     4.0   974789540   
9403        39     1500     4.0   974789727   
60382       39     1862     2.0   974787293   
11108       39     2078     3.0   974788976   
13425       39     2692     5.0   974789111   
14203       39     2947     3.0   974789327   
49571       39     3000     5.0   974789174   
63222       39     3213     5.0   974788976   

                                             title  \
18810                             Hangar 18 (1980)   
18827                       Death Race 2000 (1975)   
18832                               Troll 2 (1990)   
573                     Usual Suspects, The (1995)   
19321  Eat Drink Man Woman (Yin shi nan nu) (1994)   
25824                   Legends of the Fall (1994)   
19722             In the Name of the Father (1993)   
20123                  Beauty and the Beast (1991)   
588                     Usual Suspects, The (1995)   
45366                        Godfather, The (1972)   
7762                             Goodfellas (1990)   
9403                    Grosse Pointe Blank (1997)   
60382                            Species II (1998)   
11108                      Jungle Book, The (1967)   
13425             Run Lola Run (Lola rennt) (1998)   
14203                            Goldfinger (1964)   
49571     Princess Mononoke (Mononoke-hime) (1997)   
63222          Batman: Mask of the Phantasm (1993)   

                                                genres  
18810                           Action|Sci-Fi|Thriller  
18827                                    Action|Sci-Fi  
18832                                   Fantasy|Horror  
573                             Crime|Mystery|Thriller  
19321                             Comedy|Drama|Romance  
25824                        Drama|Romance|War|Western  
19722                                            Drama  
20123  Animation|Children|Fantasy|Musical|Romance|IMAX  
588                             Crime|Mystery|Thriller  
45366                                      Crime|Drama  
7762                                       Crime|Drama  
9403                              Comedy|Crime|Romance  
60382                                    Horror|Sci-Fi  
11108                Animation|Children|Comedy|Musical  
13425                                     Action|Crime  
14203                        Action|Adventure|Thriller  
49571         Action|Adventure|Animation|Drama|Fantasy  
63222                               Animation|Children

In [22]:
# Quick test of the recommender

lr_recommender = LinearRegressionRecommender()
lr_recommender.uses_dot_product = True
lr_recommender.fit(ml_ratings_df, None, ml_movies_df)
recommendations = lr_recommender.recommend(pd.DataFrame([[3], [5], [39]], columns=['user_id']), ml_movies_df, 10)

recommendations = pd.merge(recommendations, ml_movies_df, on='item_id', how='left')
display(recommendations)

user_action  user_adventure  user_animation  user_children  \
user_id                                                               
1           0.149254        0.119403        0.044776       0.074627   
2           0.125000        0.000000        0.000000       0.000000   
3           0.285714        0.000000        0.000000       0.000000   
4           0.017857        0.017857        0.035714       0.053571   
5           0.000000        0.000000        0.058824       0.058824   
...              ...             ...             ...            ...   
606         0.048889        0.040000        0.008889       0.022222   
607         0.148936        0.063830        0.000000       0.021277   
608         0.120172        0.055794        0.021459       0.064378   
609         0.200000        0.400000        0.000000       0.200000   
610         0.151899        0.063291        0.015823       0.015823   

         user_comedy  user_crime  user_documentary  user_drama  user_fantasy  \
user_id                                                                        
1           0.119403    0.089552          0.000000    0.059701      0.044776   
2           0.000000    0.125000          0.000000    0.375000      0.000000   
3           0.000000    0.000000          0.000000    0.000000      0.142857   
4           0.196429    0.089286          0.000000    0.267857      0.035714   
5           0.058824    0.058824          0.000000    0.176471      0.058824   
...              ...         ...               ...         ...           ...   
606         0.164444    0.066667          0.004444    0.297778      0.044444   
607         0.127660    0.085106          0.000000    0.212766      0.021277   
608         0.184549    0.077253          0.000000    0.107296      0.055794   
609         0.000000    0.000000          0.000000    0.000000      0.000000   
610         0.107595    0.069620          0.000000    0.110759      0.034810   

         user_film_noir  user_horror  user_imax  user_musical  user_mystery  \
user_id                                                                       
1              0.000000     0.000000   0.000000      0.014925      0.014925   
2              0.000000     0.000000   0.000000      0.000000      0.000000   
3              0.000000     0.142857   0.000000      0.000000      0.000000   
4              0.017857     0.000000   0.017857      0.053571      0.000000   
5              0.000000     0.000000   0.058824      0.058824      0.058824   
...                 ...          ...        ...           ...           ...   
606            0.004444     0.013333   0.008889      0.004444      0.022222   
607            0.000000     0.063830   0.000000      0.021277      0.021277   
608            0.000000     0.051502   0.008584      0.008584      0.017167   
609            0.000000     0.000000   0.000000      0.000000      0.000000   
610            0.003165     0.110759   0.031646      0.003165      0.034810   

         user_no_genres_listed  user_romance  user_sci_fi  user_thriller  \
user_id                                                                    
1                          0.0      0.074627     0.059701       0.089552   
2                          0.0      0.062500     0.062500       0.187500   
3                          0.0      0.000000     0.285714       0.142857   
4                          0.0      0.125000     0.000000       0.035714   
5                          0.0      0.176471     0.000000       0.058824   
...                        ...           ...          ...            ...   
606                        0.0      0.124444     0.031111       0.066667   
607                        0.0      0.042553     0.085106       0.063830   
608                        0.0      0.042918     0.077253       0.098712   
609                        0.0      0.000000     0.200000       0.000000   
610                        0.0      0.022152     0.085443       0.123418   

         user_war  user_wes

item_id                               title    action  adventure  \
3           4            Waiting to Exhale (1995)  0.000000       0.00   
11         12  Dracula: Dead and Loving It (1995)  0.000000       0.00   
46         50          Usual Suspects, The (1995)  0.000000       0.00   
66         74                 Bed of Roses (1996)  0.000000       0.00   
70         78          Crossing Guard, The (1995)  0.250000       0.00   
...       ...                                 ...       ...        ...   
9697   184987            A Wrinkle in Time (2018)  0.000000       0.25   
9704   185473                     Blockers (2018)  0.000000       0.00   
9721   189381                     SuperFly (2018)  0.333333       0.00   
9725   190207                         Tilt (2011)  0.000000       0.00   
9727   190213                    John From (2015)  0.000000       0.00   

      animation  children    comedy     crime  documentary     drama  fantasy  \
3           0.0      0.00  0.333333  0.000000          0.0  0.333333     0.00   
11          0.0      0.00  0.500000  0.000000          0.0  0.000000     0.00   
46          0.0      0.00  0.000000  0.333333          0.0  0.000000     0.00   
66          0.0      0.00  0.000000  0.000000          0.0  0.500000     0.00   
70          0.0      0.00  0.000000  0.250000          0.0  0.250000     0.00   
...         ...       ...       ...       ...          ...       ...      ...   
9697        0.0      0.25  0.000000  0.000000          0.0  0.000000     0.25   
9704        0.0      0.00  1.000000  0.000000          0.0  0.000000     0.00   
9721        0.0      0.00  0.000000  0.333333          0.0  0.000000     0.00   
9725        0.0      0.00  0.000000  0.000000          0.0  0.500000     0.00   
9727        0.0      0.00  0.000000  0.000000          0.0  1.000000     0.00   

      film_noir  horror  imax  musical   mystery  no_genres_listed   romance  \
3           0.0     0.0   0.0      0.0  0.000000               0.0  0.333333   
11          0.0     0.5   0.0      0.0  0.000000               0.0  0.000000   
46          0.0     0.0   0.0      0.0  0.333333               0.0  0.000000   
66          0.0     0.0   0.0      0.0  0.000000               0.0  0.500000   
70          0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   
...         ...     ...   ...      ...       ...               ...       ...   
9697        0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   
9704        0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   
9721        0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   
9725        0.0     0.0   0.0      0.0  0.000000               0.0  0.500000   
9727        0.0     0.0   0.0      0.0  0.000000               0.0  0.000000   

      sci_fi  thriller  war  western  
3       0.00  0.000000  0.0      0.0  
11      0.00  0.000000  0.0      0.0  
46      0.00  0.333333  0.0      0.0  
66      0.00  0.000000  0.0      0.0  
70      0.00  0.250000  0.0      0.0  
...      ...       ...  ...      ...  
9697    0.25  0.000000  0.0      0.0  
9704    0.00  0.000000  0.0      0.0  
9721    0.00  0.333333  0.0      0.0  
9725    0.00  0.000000  0.0      0.0  
9727    0.00  0.000000  0.0      0.0  

[1000 rows x 22 columns]

user_id item_id     score  \
0        3   51562  3.501376   
1        3    5468  3.501376   
2        3  176371  3.501376   
3        3  147384  3.501376   
4        3    2698  3.501376   
5        3    2661  3.501376   
6        3    2311  3.501376   
7        3    3926  3.425357   
8        3    4953  3.425357   
9        3    3994  3.425357   
10       5   66335  4.402264   
11       5  160848  4.402264   
12       5  151763  4.214813   
13       5   32657  4.075275   
14       5   90746  4.033668   
15       5  146028  4.007686   
16       5  147286  4.007686   
17       5    3801  3.981549   
18       5   64575  3.981549   
19       5    1964  3.981549   
20      39   66335  5.267168   
21      39  160848  5.267168   
22      39   32657  4.429362   
23      39  146028  4.296961   
24      39  147286  4.296961   
25      39   95004  4.288561   
26      39  158872  4.261897   
27      39  175431  4.261897   
28      39   48982  4.261897   
29      39  163925  4.261897   

                                                title  \
0                     Babylon 5: The Gathering (1993)   
1                    20 Million Miles to Earth (1957)   
2                            Blade Runner 2049 (2017)   
3                Doctor Who: The Runaway Bride (2007)   
4                                      Zone 39 (1997)   
5                     It Came from Outer Space (1953)   
6               2010: The Year We Make Contact (1984)   
7              Voyage to the Bottom of the Sea (1961)   
8                 People That Time Forgot, The (1977)   
9                                  Unbreakable (2000)   
10                  Afro Samurai: Resurrection (2009)   
11                              The Red Turtle (2016)   
12         Death Note Rewrite: Genshisuru Kami (2007)   
13  Man Who Planted Trees, The (Homme qui plantait...   
14                   Adventures of Tintin, The (2011)   
15  The Adventures of Sherlock Holmes and Dr. Wats...   
16  The Adventures of Sherlock Holmes and Doctor W...   
17                         Anatomy of a Murder (1959)   
18                                       Doubt (2008)   
19                                       Klute (1971)   
20                  Afro Samurai: Resurrection (2009)   
21                              The Red Turtle (2016)   
22  Man Who Planted Trees, The (Homme qui plantait...   
23  The Adventures of Sherlock Holmes and Dr. Wats...   
24  The Adventures of Sherlock Holmes and Doctor W...   
25                          Superman/Doomsday (2007)    
26                               Sausage Party (2016)   
27                       Bobik Visiting Barbos (1977)   
28                                Flushed Away (2006)   
29                       Wings, Legs and Tails (1986)   

                           genres  
0                          Sci-Fi  
1                          Sci-Fi  
2                          Sci-Fi  
3                          Sci-Fi  
4                          Sci-Fi  
5                          Sci-Fi  
6                          Sci-Fi  
7                Adventure|Sci-Fi  
8                Adventure|Sci-Fi  
9                    Drama|Sci-Fi  
10                      Animation  
11                      Animation  
12                        Mystery  
13                Animation|Drama  
14  Action|Animation|Mystery|IMAX  
15                  Crime|Mystery  
16                  Crime|Mystery  
17                  Drama|Mystery  
18                  Drama|Mystery  
19                  Drama|Mystery  
20                      Animation  
21                      Animation  
22                Animation|Drama  
23                  Crime|Mystery  
24                  Crime|Mystery  
25               Action|Animation  
26               Animation|Comedy  
27               Animation|Comedy  
28               Animation|Comedy  
29               Animation|Comedy

### Train-test split test

In [6]:
lr_recommender = LinearRegressionRecommender()

t0 = time.time()

results = [['LinearRegressionRecommender'] + list(evaluate_train_test_split_explicit(
    lr_recommender, ml_ratings_df.loc[:, ['user_id', 'item_id', 'rating']], ml_movies_df, seed=seed))]

results = pd.DataFrame(results, 
                       columns=['Recommender', 'RMSE', 'MRE', 'TRE'])

display(results)

print('Total evaluation time: {}'.format(time.time() - t0))

user_action  user_adventure  user_animation  user_children  \
user_id                                                               
1           0.142857        0.142857        0.053571       0.089286   
2           0.125000        0.000000        0.000000       0.000000   
3           0.200000        0.000000        0.000000       0.000000   
4           0.028571        0.028571        0.028571       0.057143   
5           0.000000        0.000000        0.000000       0.000000   
...              ...             ...             ...            ...   
606         0.057471        0.040230        0.011494       0.022989   
607         0.187500        0.031250        0.000000       0.000000   
608         0.109890        0.060440        0.021978       0.076923   
609         0.000000        0.500000        0.000000       0.500000   
610         0.154506        0.064378        0.012876       0.017167   

         user_comedy  user_crime  user_documentary  user_drama  user_fantasy  \
user_id                                                                        
1           0.071429    0.089286               0.0    0.053571      0.053571   
2           0.000000    0.125000               0.0    0.375000      0.000000   
3           0.000000    0.000000               0.0    0.000000      0.200000   
4           0.228571    0.085714               0.0    0.314286      0.028571   
5           0.142857    0.000000               0.0    0.285714      0.000000   
...              ...         ...               ...         ...           ...   
606         0.183908    0.068966               0.0    0.310345      0.040230   
607         0.156250    0.062500               0.0    0.250000      0.000000   
608         0.153846    0.076923               0.0    0.093407      0.071429   
609         0.000000    0.000000               0.0    0.000000      0.000000   
610         0.111588    0.072961               0.0    0.120172      0.021459   

         user_film_noir  user_horror  user_imax  user_musical  user_mystery  \
user_id                                                                       
1                   0.0     0.000000   0.000000      0.017857      0.017857   
2                   0.0     0.000000   0.000000      0.000000      0.000000   
3                   0.0     0.200000   0.000000      0.000000      0.000000   
4                   0.0     0.000000   0.000000      0.028571      0.000000   
5                   0.0     0.000000   0.000000      0.000000      0.000000   
...                 ...          ...        ...           ...           ...   
606                 0.0     0.017241   0.005747      0.000000      0.011494   
607                 0.0     0.062500   0.000000      0.000000      0.000000   
608                 0.0     0.054945   0.010989      0.010989      0.021978   
609                 0.0     0.000000   0.000000      0.000000      0.000000   
610                 0.0     0.120172   0.025751      0.004292      0.025751   

         user_no_genres_listed  user_romance  user_sci_fi  user_thriller  \
user_id                                                                    
1                          0.0      0.071429     0.053571       0.107143   
2                          0.0      0.000000     0.125000       0.250000   
3                          0.0      0.000000     0.200000       0.200000   
4                          0.0      0.114286     0.000000       0.028571   
5                          0.0      0.285714     0.000000       0.000000   
...                        ...           ...          ...            ...   
606                        0.0      0.109195     0.040230       0.057471   
607                        0.0      0.062500     0.093750       0.062500   
608                        0.0      0.049451     0.076923       0.104396   
609                        0.0      0.000000     0.000000       0.000000   
610                        0.0      0.021459     0.077253       0.128755   

         user_war  user_wes

['user_action',
 'user_adventure',
 'user_animation',
 'user_children',
 'user_comedy',
 'user_crime',
 'user_documentary',
 'user_drama',
 'user_fantasy',
 'user_film_noir',
 'user_horror',
 'user_imax',
 'user_musical',
 'user_mystery',
 'user_no_genres_listed',
 'user_romance',
 'user_sci_fi',
 'user_thriller',
 'user_war',
 'user_western']

Recommender      RMSE       MRE       TRE
0  LinearRegressionRecommender  1.016594  0.348461  0.230529

Total evaluation time: 29.65854811668396


### Leave-one-out test

In [7]:
lr_recommender = LinearRegressionRecommender()

t0 = time.time()

results = [['LinearRegressionRecommender'] + list(evaluate_leave_one_out_explicit(
    lr_recommender, ml_ratings_df.loc[:, ['user_id', 'item_id', 'rating']], ml_movies_df, seed=seed))]

results = pd.DataFrame(results, 
                       columns=['Recommender', 'RMSE', 'MRE', 'TRE'])

display(results)

print('Total evaluation time: {}'.format(time.time() - t0))

user_action  user_adventure  user_animation  user_children  \
user_id                                                               
1           0.149254        0.119403        0.044776       0.074627   
2           0.125000        0.000000        0.000000       0.000000   
3           0.285714        0.000000        0.000000       0.000000   
4           0.017857        0.017857        0.035714       0.053571   
5           0.000000        0.000000        0.058824       0.058824   
...              ...             ...             ...            ...   
606         0.048889        0.040000        0.008889       0.022222   
607         0.148936        0.063830        0.000000       0.021277   
608         0.120172        0.055794        0.021459       0.064378   
609         0.200000        0.400000        0.000000       0.200000   
610         0.151899        0.063291        0.015823       0.015823   

         user_comedy  user_crime  user_documentary  user_drama  user_fantasy  \
user_id                                                                        
1           0.119403    0.089552          0.000000    0.059701      0.044776   
2           0.000000    0.125000          0.000000    0.375000      0.000000   
3           0.000000    0.000000          0.000000    0.000000      0.142857   
4           0.196429    0.089286          0.000000    0.267857      0.035714   
5           0.058824    0.058824          0.000000    0.176471      0.058824   
...              ...         ...               ...         ...           ...   
606         0.164444    0.066667          0.004444    0.297778      0.044444   
607         0.127660    0.085106          0.000000    0.212766      0.021277   
608         0.184549    0.077253          0.000000    0.107296      0.055794   
609         0.000000    0.000000          0.000000    0.000000      0.000000   
610         0.107595    0.069620          0.000000    0.110759      0.034810   

         user_film_noir  user_horror  user_imax  user_musical  user_mystery  \
user_id                                                                       
1              0.000000     0.000000   0.000000      0.014925      0.014925   
2              0.000000     0.000000   0.000000      0.000000      0.000000   
3              0.000000     0.142857   0.000000      0.000000      0.000000   
4              0.017857     0.000000   0.017857      0.053571      0.000000   
5              0.000000     0.000000   0.058824      0.058824      0.058824   
...                 ...          ...        ...           ...           ...   
606            0.004444     0.013333   0.008889      0.004444      0.022222   
607            0.000000     0.063830   0.000000      0.021277      0.021277   
608            0.000000     0.051502   0.008584      0.008584      0.017167   
609            0.000000     0.000000   0.000000      0.000000      0.000000   
610            0.003165     0.110759   0.031646      0.003165      0.034810   

         user_no_genres_listed  user_romance  user_sci_fi  user_thriller  \
user_id                                                                    
1                          0.0      0.074627     0.059701       0.089552   
2                          0.0      0.062500     0.062500       0.187500   
3                          0.0      0.000000     0.285714       0.142857   
4                          0.0      0.125000     0.000000       0.035714   
5                          0.0      0.176471     0.000000       0.058824   
...                        ...           ...          ...            ...   
606                        0.0      0.124444     0.031111       0.066667   
607                        0.0      0.042553     0.085106       0.063830   
608                        0.0      0.042918     0.077253       0.098712   
609                        0.0      0.000000     0.200000       0.000000   
610                        0.0      0.022152     0.085443       0.123418   

         user_war  user_wes

['user_action',
 'user_adventure',
 'user_animation',
 'user_children',
 'user_comedy',
 'user_crime',
 'user_documentary',
 'user_drama',
 'user_fantasy',
 'user_film_noir',
 'user_horror',
 'user_imax',
 'user_musical',
 'user_mystery',
 'user_no_genres_listed',
 'user_romance',
 'user_sci_fi',
 'user_thriller',
 'user_war',
 'user_western']

user_action  user_adventure  user_animation  user_children  \
user_id                                                               
1           0.149254        0.119403        0.044776       0.074627   
2           0.125000        0.000000        0.000000       0.000000   
3           0.285714        0.000000        0.000000       0.000000   
4           0.017857        0.017857        0.035714       0.053571   
5           0.000000        0.000000        0.058824       0.058824   
...              ...             ...             ...            ...   
606         0.048889        0.040000        0.008889       0.022222   
607         0.148936        0.063830        0.000000       0.021277   
608         0.120172        0.055794        0.021459       0.064378   
609         0.200000        0.400000        0.000000       0.200000   
610         0.151899        0.063291        0.015823       0.015823   

         user_comedy  user_crime  user_documentary  user_drama  user_fantasy  \
user_id                                                                        
1           0.119403    0.089552          0.000000    0.059701      0.044776   
2           0.000000    0.125000          0.000000    0.375000      0.000000   
3           0.000000    0.000000          0.000000    0.000000      0.142857   
4           0.196429    0.089286          0.000000    0.267857      0.035714   
5           0.058824    0.058824          0.000000    0.176471      0.058824   
...              ...         ...               ...         ...           ...   
606         0.164444    0.066667          0.004444    0.297778      0.044444   
607         0.127660    0.085106          0.000000    0.212766      0.021277   
608         0.184549    0.077253          0.000000    0.107296      0.055794   
609         0.000000    0.000000          0.000000    0.000000      0.000000   
610         0.107595    0.069620          0.000000    0.110759      0.034810   

         user_film_noir  user_horror  user_imax  user_musical  user_mystery  \
user_id                                                                       
1              0.000000     0.000000   0.000000      0.014925      0.014925   
2              0.000000     0.000000   0.000000      0.000000      0.000000   
3              0.000000     0.142857   0.000000      0.000000      0.000000   
4              0.017857     0.000000   0.017857      0.053571      0.000000   
5              0.000000     0.000000   0.058824      0.058824      0.058824   
...                 ...          ...        ...           ...           ...   
606            0.004444     0.013333   0.008889      0.004444      0.022222   
607            0.000000     0.063830   0.000000      0.021277      0.021277   
608            0.000000     0.051502   0.008584      0.008584      0.017167   
609            0.000000     0.000000   0.000000      0.000000      0.000000   
610            0.003165     0.110759   0.031646      0.003165      0.034810   

         user_no_genres_listed  user_romance  user_sci_fi  user_thriller  \
user_id                                                                    
1                          0.0      0.074627     0.059701       0.089552   
2                          0.0      0.062500     0.062500       0.187500   
3                          0.0      0.000000     0.285714       0.142857   
4                          0.0      0.125000     0.000000       0.035714   
5                          0.0      0.176471     0.000000       0.058824   
...                        ...           ...          ...            ...   
606                        0.0      0.124444     0.031111       0.066667   
607                        0.0      0.042553     0.085106       0.063830   
608                        0.0      0.042918     0.077253       0.098712   
609                        0.0      0.000000     0.200000       0.000000   
610                        0.0      0.022152     0.085443       0.123418   

         user_war  user_wes

['user_action',
 'user_adventure',
 'user_animation',
 'user_children',
 'user_comedy',
 'user_crime',
 'user_documentary',
 'user_drama',
 'user_fantasy',
 'user_film_noir',
 'user_horror',
 'user_imax',
 'user_musical',
 'user_mystery',
 'user_no_genres_listed',
 'user_romance',
 'user_sci_fi',
 'user_thriller',
 'user_war',
 'user_western']

user_action  user_adventure  user_animation  user_children  \
user_id                                                               
1           0.149254        0.119403        0.044776       0.074627   
2           0.125000        0.000000        0.000000       0.000000   
3           0.285714        0.000000        0.000000       0.000000   
4           0.017857        0.017857        0.035714       0.053571   
5           0.000000        0.000000        0.058824       0.058824   
...              ...             ...             ...            ...   
606         0.048889        0.040000        0.008889       0.022222   
607         0.148936        0.063830        0.000000       0.021277   
608         0.120172        0.055794        0.021459       0.064378   
609         0.200000        0.400000        0.000000       0.200000   
610         0.151899        0.063291        0.015823       0.015823   

         user_comedy  user_crime  user_documentary  user_drama  user_fantasy  \
user_id                                                                        
1           0.119403    0.089552          0.000000    0.059701      0.044776   
2           0.000000    0.125000          0.000000    0.375000      0.000000   
3           0.000000    0.000000          0.000000    0.000000      0.142857   
4           0.196429    0.089286          0.000000    0.267857      0.035714   
5           0.058824    0.058824          0.000000    0.176471      0.058824   
...              ...         ...               ...         ...           ...   
606         0.164444    0.066667          0.004444    0.297778      0.044444   
607         0.127660    0.085106          0.000000    0.212766      0.021277   
608         0.184549    0.077253          0.000000    0.107296      0.055794   
609         0.000000    0.000000          0.000000    0.000000      0.000000   
610         0.107595    0.069620          0.000000    0.110759      0.034810   

         user_film_noir  user_horror  user_imax  user_musical  user_mystery  \
user_id                                                                       
1              0.000000     0.000000   0.000000      0.014925      0.014925   
2              0.000000     0.000000   0.000000      0.000000      0.000000   
3              0.000000     0.142857   0.000000      0.000000      0.000000   
4              0.017857     0.000000   0.017857      0.053571      0.000000   
5              0.000000     0.000000   0.058824      0.058824      0.058824   
...                 ...          ...        ...           ...           ...   
606            0.004444     0.013333   0.008889      0.004444      0.022222   
607            0.000000     0.063830   0.000000      0.021277      0.021277   
608            0.000000     0.051502   0.008584      0.008584      0.017167   
609            0.000000     0.000000   0.000000      0.000000      0.000000   
610            0.003165     0.110759   0.031646      0.003165      0.034810   

         user_no_genres_listed  user_romance  user_sci_fi  user_thriller  \
user_id                                                                    
1                          0.0      0.074627     0.059701       0.089552   
2                          0.0      0.062500     0.062500       0.187500   
3                          0.0      0.000000     0.285714       0.142857   
4                          0.0      0.125000     0.000000       0.035714   
5                          0.0      0.176471     0.000000       0.058824   
...                        ...           ...          ...            ...   
606                        0.0      0.124444     0.031111       0.066667   
607                        0.0      0.042553     0.085106       0.063830   
608                        0.0      0.042918     0.077253       0.098712   
609                        0.0      0.000000     0.200000       0.000000   
610                        0.0      0.022152     0.085443       0.123418   

         user_war  user_wes

...

['user_action',
 'user_adventure',
 'user_animation',
 'user_children',
 'user_comedy',
 'user_crime',
 'user_documentary',
 'user_drama',
 'user_fantasy',
 'user_film_noir',
 'user_horror',
 'user_imax',
 'user_musical',
 'user_mystery',
 'user_no_genres_listed',
 'user_romance',
 'user_sci_fi',
 'user_thriller',
 'user_war',
 'user_western']

user_action  user_adventure  user_animation  user_children  \
user_id                                                               
1           0.149254        0.119403        0.044776       0.074627   
2           0.125000        0.000000        0.000000       0.000000   
3           0.285714        0.000000        0.000000       0.000000   
4           0.017857        0.017857        0.035714       0.053571   
5           0.000000        0.000000        0.058824       0.058824   
...              ...             ...             ...            ...   
606         0.048889        0.040000        0.008889       0.022222   
607         0.148936        0.063830        0.000000       0.021277   
608         0.120172        0.055794        0.021459       0.064378   
609         0.200000        0.400000        0.000000       0.200000   
610         0.151899        0.063291        0.015823       0.015823   

         user_comedy  user_crime  user_documentary  user_drama  user_fantasy  \
user_id                                                                        
1           0.119403    0.089552          0.000000    0.059701      0.044776   
2           0.000000    0.125000          0.000000    0.375000      0.000000   
3           0.000000    0.000000          0.000000    0.000000      0.142857   
4           0.196429    0.089286          0.000000    0.267857      0.035714   
5           0.058824    0.058824          0.000000    0.176471      0.058824   
...              ...         ...               ...         ...           ...   
606         0.164444    0.066667          0.004444    0.297778      0.044444   
607         0.127660    0.085106          0.000000    0.212766      0.021277   
608         0.184549    0.077253          0.000000    0.107296      0.055794   
609         0.000000    0.000000          0.000000    0.000000      0.000000   
610         0.107595    0.069620          0.000000    0.110759      0.034810   

         user_film_noir  user_horror  user_imax  user_musical  user_mystery  \
user_id                                                                       
1              0.000000     0.000000   0.000000      0.014925      0.014925   
2              0.000000     0.000000   0.000000      0.000000      0.000000   
3              0.000000     0.142857   0.000000      0.000000      0.000000   
4              0.017857     0.000000   0.017857      0.053571      0.000000   
5              0.000000     0.000000   0.058824      0.058824      0.058824   
...                 ...          ...        ...           ...           ...   
606            0.004444     0.013333   0.008889      0.004444      0.022222   
607            0.000000     0.063830   0.000000      0.021277      0.021277   
608            0.000000     0.051502   0.008584      0.008584      0.017167   
609            0.000000     0.000000   0.000000      0.000000      0.000000   
610            0.003165     0.110759   0.031646      0.003165      0.034810   

         user_no_genres_listed  user_romance  user_sci_fi  user_thriller  \
user_id                                                                    
1                          0.0      0.074627     0.059701       0.089552   
2                          0.0      0.062500     0.062500       0.187500   
3                          0.0      0.000000     0.285714       0.142857   
4                          0.0      0.125000     0.000000       0.035714   
5                          0.0      0.176471     0.000000       0.058824   
...                        ...           ...          ...            ...   
606                        0.0      0.124444     0.031111       0.066667   
607                        0.0      0.042553     0.085106       0.063830   
608                        0.0      0.042918     0.077253       0.098712   
609                        0.0      0.000000     0.200000       0.000000   
610                        0.0      0.022152     0.085443       0.123418   

         user_war  user_wes

['user_action',
 'user_adventure',
 'user_animation',
 'user_children',
 'user_comedy',
 'user_crime',
 'user_documentary',
 'user_drama',
 'user_fantasy',
 'user_film_noir',
 'user_horror',
 'user_imax',
 'user_musical',
 'user_mystery',
 'user_no_genres_listed',
 'user_romance',
 'user_sci_fi',
 'user_thriller',
 'user_war',
 'user_western']

Recommender      RMSE       MRE       TRE
0  LinearRegressionRecommender  1.045415  0.401399  0.242301

Total evaluation time: 44.599799156188965


# TF-IDF Recommender
TF-IDF stands for term frequency–inverse document frequency. Typically Tf-IDF method is used to assign keywords (words describing the gist of a document) to documents in a corpus of documents.

In our case we will treat users as documents and genres as words.

Term-frequency is given by the following formula:
<center>
$$
    \text{tf}(g, u) = f_{g, u}
$$
</center>
where $f_{g, i}$ is the number of times genre $g$ appear for movies watched by user $u$.

Inverse document frequency is defined as follows:
<center>
$$
    \text{idf}(g) = \log \frac{N}{n_g}
$$
</center>
where $N$ is the number of users and $n_g$ is the number of users with $g$ in their genres list.

Finally, tf-idf is defined as follows:
<center>
$$
    \text{tfidf}(g, u) = \text{tf}(g, u) \cdot \text{idf}(g)
$$
</center>

In our case we will measure how often a given genre appears for movies watched by a given user vs how often it appears for all users. To obtain a movie score we will take the average of its genres' scores for this user.

In [8]:
from sklearn.feature_extraction.text import TfidfVectorizer

class TFIDFRecommender(Recommender):
    """
    Recommender based on the TF-IDF method.
    """
    
    def __init__(self):
        """
        Initialize base recommender params and variables.
        """
        self.tfidf_scores = None
    
    def fit(self, interactions_df, users_df, items_df):
        """
        Training of the recommender.
        
        :param pd.DataFrame interactions_df: DataFrame with recorded interactions between users and items 
            defined by user_id, item_id and features of the interaction.
        :param pd.DataFrame users_df: DataFrame with users and their features defined by user_id and the user feature columns.
        :param pd.DataFrame items_df: DataFrame with items and their features defined by item_id and the item feature columns.
        """
        
        self.tfidf_scores = defaultdict(lambda: 0.0)

        # Prepare the corpus for tfidf calculation
        
        interactions_df = pd.merge(interactions_df, items_df, on='item_id')
#         print("Training set")
#         display(interactions_df.head(10))
#         print()
        user_genres = interactions_df.loc[:, ['user_id', 'genres']]
        user_genres.loc[:, 'genres'] = user_genres['genres'].str.replace("-", "_", regex=False)
        user_genres.loc[:, 'genres'] = user_genres['genres'].str.replace(" ", "_", regex=False)
        user_genres = user_genres.groupby('user_id').aggregate(lambda x: "|".join(x))
        user_genres.loc[:, 'genres'] = user_genres['genres'].str.replace("|", " ", regex=False)
#         print("User genres")
#         display(user_genres.head(10))
#         print()
        user_ids = user_genres.index.tolist()
        genres_corpus = user_genres['genres'].tolist()
#         print("Genres corpus")
#         print(genres_corpus)
#         print()
        
        # Calculate tf-idf scores
        
        vectorizer = TfidfVectorizer()
        tfidf_scores = vectorizer.fit_transform(genres_corpus)
        
        print(tfidf_scores.shape[0])
        # Transform results into a dict {(user_id, genre): score}
        
        for u in range(tfidf_scores.shape[0]):
            for g in range(tfidf_scores.shape[1]):
                self.tfidf_scores[(user_ids[u], vectorizer.get_feature_names()[g])] = tfidf_scores[u, g]

#         print("TF-IDF scores")
#         print(self.tfidf_scores)
#         print()
    
    def recommend(self, users_df, items_df, n_recommendations=1):
        """
        Serving of recommendations. Scores items in items_df for each user in users_df and returns 
        top n_recommendations for each user.
        
        :param pd.DataFrame users_df: DataFrame with users and their features for which recommendations should be generated.
        :param pd.DataFrame items_df: DataFrame with items and their features which should be scored.
        :param int n_recommendations: Number of recommendations to be returned for each user.
        :return: DataFrame with user_id, item_id and score as columns returning n_recommendations top recommendations 
            for each user.
        :rtype: pd.DataFrame
        """
        
        recommendations = pd.DataFrame(columns=['user_id', 'item_id', 'score'])
        
        # Transform genres to a unified form used by the vectorizer
        
        items_df = items_df.copy()
        items_df.loc[:, 'genres'] = items_df['genres'].str.replace("-", "_", regex=False)
        items_df.loc[:, 'genres'] = items_df['genres'].str.replace(" ", "_", regex=False)
        items_df.loc[:, 'genres'] = items_df['genres'].str.lower()
        items_df.loc[:, 'genres'] = items_df['genres'].str.split("|")
                
        # Score items    
        
        for uix, user in users_df.iterrows():
            items = []
            for iix, item in items_df.iterrows():
                score = 0.0
                for genre in item['genres']:
                    score += self.tfidf_scores[(user['user_id'], genre)]
                score /= len(item['genres'])
                items.append((item['item_id'], score))
                
            items = sorted(items, key=lambda x: x[1], reverse=True)
            user_recommendations = pd.DataFrame({'user_id': user['user_id'],
                                                 'item_id': [item[0] for item in items][:n_recommendations],
                                                 'score': [item[1] for item in items][:n_recommendations]})

            recommendations = pd.concat([recommendations, user_recommendations])

        return recommendations

In [9]:
# Print movies watched by user 3, 5, 39

active_user_movies = ml_df.loc[
    (ml_df['user_id'] == 3) | (ml_df['user_id'] == 5) | (ml_df['user_id'] == 39)].sort_values(['user_id', 'item_id'])
print("Active users history")
display(active_user_movies)

Active users history


user_id  item_id  rating   timestamp  \
18810        3     5181     5.0  1306463718   
18827        3     7991     5.0  1306463684   
18832        3    70946     5.0  1306463815   
573          5       50     4.0   847434881   
19321        5      232     4.0   847435292   
25824        5      266     1.0   847435311   
19722        5      475     5.0   847435311   
20123        5      595     5.0   847434832   
588         39       50     5.0   974788030   
45366       39      858     4.0   974789111   
7762        39     1213     4.0   974789540   
9403        39     1500     4.0   974789727   
60382       39     1862     2.0   974787293   
11108       39     2078     3.0   974788976   
13425       39     2692     5.0   974789111   
14203       39     2947     3.0   974789327   
49571       39     3000     5.0   974789174   
63222       39     3213     5.0   974788976   

                                             title  \
18810                             Hangar 18 (1980)   
18827                       Death Race 2000 (1975)   
18832                               Troll 2 (1990)   
573                     Usual Suspects, The (1995)   
19321  Eat Drink Man Woman (Yin shi nan nu) (1994)   
25824                   Legends of the Fall (1994)   
19722             In the Name of the Father (1993)   
20123                  Beauty and the Beast (1991)   
588                     Usual Suspects, The (1995)   
45366                        Godfather, The (1972)   
7762                             Goodfellas (1990)   
9403                    Grosse Pointe Blank (1997)   
60382                            Species II (1998)   
11108                      Jungle Book, The (1967)   
13425             Run Lola Run (Lola rennt) (1998)   
14203                            Goldfinger (1964)   
49571     Princess Mononoke (Mononoke-hime) (1997)   
63222          Batman: Mask of the Phantasm (1993)   

                                                genres  
18810                           Action|Sci-Fi|Thriller  
18827                                    Action|Sci-Fi  
18832                                   Fantasy|Horror  
573                             Crime|Mystery|Thriller  
19321                             Comedy|Drama|Romance  
25824                        Drama|Romance|War|Western  
19722                                            Drama  
20123  Animation|Children|Fantasy|Musical|Romance|IMAX  
588                             Crime|Mystery|Thriller  
45366                                      Crime|Drama  
7762                                       Crime|Drama  
9403                              Comedy|Crime|Romance  
60382                                    Horror|Sci-Fi  
11108                Animation|Children|Comedy|Musical  
13425                                     Action|Crime  
14203                        Action|Adventure|Thriller  
49571         Action|Adventure|Animation|Drama|Fantasy  
63222                               Animation|Children

In [10]:
# Quick test of the recommender

tfidf_recommender = TFIDFRecommender()
tfidf_recommender.fit(ml_ratings_df, None, ml_movies_df)
recommendations = tfidf_recommender.recommend(pd.DataFrame([[3], [5], [39]], columns=['user_id']), ml_movies_df, 10)

recommendations = pd.merge(recommendations, ml_movies_df, on='item_id', how='left')
print("Recommendations")
display(recommendations)

598


AttributeError: 'TfidfVectorizer' object has no attribute 'get_feature_names'

### Train-test split test

In [ ]:
tfidf_recommender = TFIDFRecommender()

t0 = time.time()

results = [['TFIDFRecommender'] + list(evaluate_train_test_split_implicit(
    tfidf_recommender, ml_ratings_df.loc[:, ['user_id', 'item_id']], ml_movies_df))]

results = pd.DataFrame(results, 
                       columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(results)

print('Total evaluation time: {}'.format(time.time() - t0))

### Leave-one-out test

In [ ]:
tfidf_recommender = TFIDFRecommender()

t0 = time.time()

results = [['TFIDFRecommender'] + list(evaluate_leave_one_out_implicit(
    tfidf_recommender, ml_ratings_df.loc[:, ['user_id', 'item_id']], ml_movies_df, max_evals=300, seed=6789))]

results = pd.DataFrame(results, 
                       columns=['Recommender', 'HR@1', 'HR@3', 'HR@5', 'HR@10', 'NDCG@1', 'NDCG@3', 'NDCG@5', 'NDCG@10'])

display(results)

print('Total evaluation time: {}'.format(time.time() - t0))